prepare data

In [0]:
CREATE TABLE IF NOT EXISTS ecommerce_sales
(
	invoiceno VARCHAR(30)   
	,stockcode VARCHAR(30)   
	,description VARCHAR(60)    
	,quantity DOUBLE PRECISION   
	,invoicedate VARCHAR(30)    
	,unitprice    DOUBLE PRECISION
	,customerid BIGINT    
	,country VARCHAR(25)    
)
;
Copy ecommerce_sales
From 's3://redshift-ml-multiclass/ecommerce_data.txt'
iam_role default delimiter '\t' IGNOREHEADER 1 region 'us-east-1' maxerror 100;

create table ecommerce_sales_data as (
  select
    t1.stockcode,
    t1.description,
    t1.invoicedate,
    t1.customerid,
    t1.country,
    t1.sales_amt,
    cast(random() * 100 as int) as data_group_id
  from
    (
      select
        stockcode,
        description,
        invoicedate,
        customerid,
        country,
        sum(quantity * unitprice) as sales_amt
      from
        ecommerce_sales
      group by
        1,
        2,
        3,
        4,
        5
    ) t1
);
 
create table ecommerce_sales_training as (
  select
    a.customerid,
    a.country,
    a.stockcode,
    a.description,
    a.invoicedate,
    a.sales_amt,
    (b.nbr_months_active) as nbr_months_active
  from
    ecommerce_sales_data a
    inner join (
      select
        customerid,
        count(
          distinct(
            DATE_PART(y, cast(invoicedate as date)) || '-' || LPAD(
              DATE_PART(mon, cast(invoicedate as date)),
              2,
              '00'
            )
          )
        ) as nbr_months_active
      from
        ecommerce_sales_data
      group by
        1
    ) b on a.customerid = b.customerid
  where
    a.data_group_id < 80
);
 
create table ecommerce_sales_validation as (
  select
    a.customerid,
    a.country,
    a.stockcode,
    a.description,
    a.invoicedate,
    a.sales_amt,
    (b.nbr_months_active) as nbr_months_active
  from
    ecommerce_sales_data a
    inner join (
      select
        customerid,
        count(
          distinct(
            DATE_PART(y, cast(invoicedate as date)) || '-' || LPAD(
              DATE_PART(mon, cast(invoicedate as date)),
              2,
              '00'
            )
          )
        ) as nbr_months_active
      from
        ecommerce_sales_data
      group by
        1
    ) b on a.customerid = b.customerid
  where
    a.data_group_id between 80
    and 90
);
 
create table ecommerce_sales_prediction as (
  select
    customerid,
    country,
    stockcode,
    description,
    invoicedate,
    sales_amt
  from
    ecommerce_sales_data
  where
    data_group_id > 90);

create model - replace <<your-amazon-s3-bucket>> with your S3 bucket

In [0]:
create model ecommerce_customer_activity
from
  (
select   
  customerid,
  country,
  stockcode,
  description,
  invoicedate,
  sales_amt,
  nbr_months_active  
 from ecommerce_sales_training)
 TARGET nbr_months_active FUNCTION predict_customer_activity
 IAM_ROLE default
 problem_type MULTICLASS_CLASSIFICATION  
  SETTINGS (
    S3_BUCKET '<<your-amazon-s3-bucket>>',
    S3_GARBAGE_COLLECT OFF,
    MAX_RUNTIME 9600
    
  );

show model output

In [0]:
Show model ecommerce_customer_activity;

run validation query

In [0]:
select 
 cast(sum(t1.match)as decimal(7,2)) as predicted_matches
,cast(sum(t1.nonmatch) as decimal(7,2)) as predicted_non_matches
,cast(sum(t1.match + t1.nonmatch) as decimal(7,2))  as total_predictions
,predicted_matches / total_predictions as pct_accuracy
from 
(select   
  customerid,
  country,
  stockcode,
  description,
  invoicedate,
  sales_amt,
  nbr_months_active,
  predict_customer_activity(customerid, country, stockcode, description, invoicedate, sales_amt) as predicted_months_active,
  case when nbr_months_active = predicted_months_active then 1
      else 0 end as match,
  case when nbr_months_active <> predicted_months_active then 1
    else 0 end as nonmatch
  from ecommerce_sales_validation
  )t1;

run inference query

In [0]:
select 
  customerid,  
  predict_customer_activity(customerid, country, stockcode, description, invoicedate, sales_amt) as predicted_months_active
  from ecommerce_sales_prediction
 where predicted_months_active >=7
 group by 1,2
 limit 10;

run probabality queries

In [0]:
select 
customerid,
predict_customer_activity_prob(customerid, country, stockcode, description, invoicedate, sales_amt) as probabilities
 from ecommerce_sales_prediction
where customerid in (13993, 17581)
group by 1,2;

In [0]:
Select t1.customerid, prediction.labels[0], prediction.probabilities[0]
from (select 
  customerid,
  predict_customer_activity_prob(customerid, country, stockcode, description, invoicedate, sales_amt) as prediction
  from ecommerce_sales_prediction
 where customerid in(13993, 17581)
)t1
group by 1,2,3
order by 1;

In [0]:
Select t1.customerid, prediction.labels[0] as labels, cast(prediction.probabilities[0] as decimal(4,2)) as probabilities
from (select 
  customerid,
  predict_customer_activity_prob(customerid, country, stockcode, description, invoicedate, sales_amt) as prediction
  from ecommerce_sales_prediction
 where customerid in(13993, 17581)
)t1
group by 1,2,3
order by 1;

In [0]:
Select cast(prediction.probabilities[0] as decimal(4,1)) as probabilities, count(*) 
from (select 
  customerid,
  predict_customer_activity_prob(customerid, country, stockcode, description, invoicedate, sales_amt) as prediction
  from ecommerce_sales_prediction
)t1
group by 1
order by 1 desc;

run explainability report

In [0]:
select json_table.report.explanations.kernel_shap.label0.global_shap_values 
from (select explain_model('ecommerce_customer_activity') as report) as json_table;